In [ ]:
pip install requests

In [76]:
import numpy as np
from sklearn.feature_extraction import DictVectorizer
import pandas as pd
import joblib
import re
from collections import Counter
from scipy import sparse
import collections
from sklearn.model_selection import train_test_split

all_tweets = joblib.load('./mps_all_tweets.pckle')

In [77]:
def sanitise(mps_tweets_df):
    # Sanitise author column
    mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.lower())
    mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.split()[0])

    author_contents_mps_tweets_df = mps_tweets_df[['author', 'contents']].copy()

    def extract_hash_tags(s):
        return set([re.sub(r"#+", "#", k) for k in set(
            [re.sub(r"(\W+)$", "", j, flags=re.UNICODE) for j in set([i for i in s.split() if i.startswith("#")])])])

    dict_of_mps = {k: v for k, v in author_contents_mps_tweets_df.groupby('author')['contents']}
    new_dict_of_mps = {}

    for k, v in dict_of_mps.items():
        vals = []
        for val in v:
            vals.append(extract_hash_tags(val))
        new_dict_of_mps[k] = vals

    for k in new_dict_of_mps.keys():
        new_dict_of_mps[k] = [item for sublist in new_dict_of_mps[k] for item in sublist]

    '''
    for k in new_dict_of_mps.keys():
        new_dict_of_mps[k] = dict(Counter(new_dict_of_mps[k]))
    '''
    return new_dict_of_mps

In [ ]:
df = pd.DataFrame.from_dict(all_tweets[0]['posts'])

hashtag_df = sanitise(df)

In [ ]:
print(all_tweets[365])

In [78]:
all_hashtags = []
count = 0
for dict_of_tweets in all_tweets[:-1]:
    all_hashtags.append(sanitise(pd.DataFrame.from_dict(dict_of_tweets['posts'])))
    count += 1

In [79]:
final_hashtags_dict = {}
for dict_of_hashtags in all_hashtags:
    for k,v in dict_of_hashtags.items():
        if k in final_hashtags_dict.keys():
            val = final_hashtags_dict[k]
            if val != None:
                val = val + v
            else:
                val = v
            final_hashtags_dict[k] = val
        else:
            final_hashtags_dict[k] = v

In [ ]:
type(all_hashtags)

In [ ]:
final_hashtags_dict

In [ ]:
print(all_hashtags[2].items())

In [80]:
'''
for k in final_hashtags_dict.keys():
    #final_hashtags_dict[k] = [item for sublist in final_hashtags_dict[k] for item in sublist]
    has_list = any(isinstance(i, list) for i in final_hashtags_dict[k])
    if has_list:
        final_hashtags_dict[k] = list(np.concatenate(final_hashtags_dict[k]).flat)
'''
for k in final_hashtags_dict.keys():
    final_hashtags_dict[k] = dict(Counter(final_hashtags_dict[k]))

In [ ]:
mps_dict_for_conc = final_hashtags_dict

In [ ]:
total_dict = {**mps_dict_for_conc, **final_hashtags_dict}

In [ ]:
joblib.dump(list(final_hashtags_dict.keys()), './order.pckle')

In [201]:
final_hashtags_dict

{'alison_mcgovern': {'#NHS': 3,
  '#proud': 1,
  '#thisgirlcan': 4,
  '#votelabour': 7,
  '#fb': 22,
  '#syria': 1,
  '#pmqs': 3,
  '#syrianchildren': 1,
  '#lordwoodofanfield': 1,
  '#Brexit': 14,
  '#PMQs': 4,
  '#RefugeesWelcome': 2,
  '#DignityIsPriceless': 1,
  '#FundUNRWA': 1,
  '#VoteLabour': 3,
  '#YNWA': 8,
  '#Syria': 9,
  '#Vote100': 1,
  '#progressrequired': 1,
  '#TimeFlies': 1,
  '#justathought': 1,
  '#ynwa': 9,
  '#not': 2,
  '#newferry': 16,
  '#Ghouta': 2,
  '#organdonation': 1,
  '#SaveGhouta': 1,
  '#marr': 1,
  '#NWWOMEN18': 2,
  '#moreincommon': 4,
  '#IWD2018': 2,
  '#SpringStatement': 5,
  '#FamiliesTogether': 1,
  '#immigration': 2,
  '#LabourDoorstep': 1,
  '#northern': 1,
  '#angry': 1,
  '#football': 3,
  '#womenssport': 3,
  '#womensfooty': 3,
  '#labourdoorstep': 2,
  '#lfcfamily': 1,
  '#lfc': 5,
  '#Aleppo': 1,
  '#JFT96': 1,
  '#lovelikeJo': 4,
  '#WithSyria': 1,
  '#labourfamily': 1,
  '#ShakespeareDay': 1,
  '#wirral': 3,
  '#PAC18': 1,
  '#childpover

In [ ]:
vectorizer = DictVectorizer()

hashtags = list(final_hashtags_dict.values())

sparse_adjacency_matrix = vectorizer.fit_transform(hashtags)
hashtags_df = pd.DataFrame(sparse_adjacency_matrix.todense(), index=final_hashtags_dict.keys()
                           , columns=vectorizer.get_feature_names())

#sparse_hashtags_df = hashtags_df.to_sparse(fill_value=0.0)

sparse_csr_matrix = sparse.csr_matrix(hashtags_df.values)

joblib.dump(sparse_csr_matrix, './ind.mps.allx') 

In [ ]:
import requests

def get_votes(url):
    response = requests.get(url).json()
    votes = response['result']['primaryTopic']['vote']
    
    return {vote['memberPrinted']['_value']: 
                (1 if vote['type'] == 'http://data.parliament.uk/schema/parl#AyeVote' else 0)
                 for vote in votes }

brexit_votes_2017 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/759161.json')

#health_votes = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/1126420.json')

'''
brexit_votes = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/1107737.json')
brexit_votes2 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/1061010.json')
brexit_votes3 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/824379.json')
brexit_votes4 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/759161.json')

brexit12 = {**brexit_votes, **brexit_votes2}
brexit123 = {**brexit12, **brexit_votes3}
final_brexit = {**brexit123, **brexit_votes4}
'''

brexit_vote_2019 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/1107737.json')

In [ ]:
universal_credit_votes1 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/938441.json')
universal_credit_votes2 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/989442.json')
universal_credit_votes3 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/860992.json')

for k in universal_credit_votes3.keys():
    universal_credit_votes3[k] = universal_credit_votes3[k] ^ 1

universal_credit_votes4 = {**universal_credit_votes1, **universal_credit_votes2}
universal_credit_votes = {**universal_credit_votes4, **universal_credit_votes3}

In [ ]:
no_confidence_votes = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/1042258.json')

In [ ]:
health_votes_1 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/910143.json')
health_votes_2 = get_votes('http://lda.data.parliament.uk/commonsdivisions/id/1126420.json')

health_votes = {**health_votes_1, **health_votes_2}

In [ ]:
get_handles = joblib.load('./all_vote_labels.y')
handles = list(get_handles.keys())

In [ ]:
handles

In [ ]:
names = list(brexit_votes_2017)

In [ ]:
names

In [ ]:
mp_id_name_handle_mapping_df = pd.read_csv('mp_id_name_handle_mapping.csv')
mp_name_handle_mapping = dict(zip(list(mp_id_name_handle_mapping_df['label']), list(mp_id_name_handle_mapping_df['twitter_handles'])))
mp_name_handle_mapping.update({k: v.lower() for k, v in mp_name_handle_mapping.items()})
len(mp_name_handle_mapping)

In [ ]:
extracted_handles = []
for h in handles:
    temp = h.split()
    extracted_handles.append(temp[0])

In [ ]:
set(extracted_handles).difference(set(mp_name_handle_mapping.values()))

In [ ]:
set(mp_name_handle_mapping.values()).difference(set(extracted_handles))

In [ ]:
brexit_vote_2019

In [ ]:
mp_name_handle_df = pd.DataFrame.from_dict(mp_name_handle_mapping.items())
mp_name_handle_df.to_csv('handle_name_mapping.csv', index=False, columns=None)

In [ ]:
brexit_votes_df = pd.read_csv('brexit_votes_all.csv', names=['Name','Vote'])

In [ ]:
brexit_votes_df = pd.DataFrame(brexit_vote_2019.items(), columns=['Name', 'Vote'])

In [ ]:
health_votes_df = pd.DataFrame(health_votes.items(), columns=['Name','Vote'])

In [ ]:
brexit_votes_df = pd.DataFrame(brexit_votes_2017.items(), columns=['Name', 'Vote'])

In [ ]:
no_confidence_votes_df = pd.DataFrame(no_confidence_votes.items(), columns=['Name','Vote'])

In [ ]:
no_confidence_votes_df

In [ ]:
mp_name_handle_mapping_df = pd.read_csv('handle_name_mapping_final.csv', names=['Name', 'Handle'])
mp_name_handle_mapping_df

In [ ]:
mp_handle_name_mapping_dict = mp_name_handle_mapping_df.to_dict('list')
brexit_2019_votes_dict = brexit_votes_df.to_dict('list')

In [ ]:
mp_names_vote = brexit_2019_votes_dict['Name']

In [ ]:
mp_votes = brexit_2019_votes_dict['Vote']

In [ ]:
mp_names = mp_handle_name_mapping_dict['Name']

In [ ]:
mp_handles = mp_handle_name_mapping_dict['Handle']

In [ ]:
mp_handles

In [ ]:
mp_name_handle_mapping_dict = dict(zip(mp_names, mp_handles))

In [ ]:
mp_names_vote = [l[1:] for l in mp_names_vote[1:]]

In [ ]:
mp_names_vote = ['Nigel Adams'] + mp_names_vote
mp_names_vote

In [ ]:
mp_name_vote_mapping_dict = dict(zip(mp_names_vote, mp_votes))

In [ ]:
mp_name_vote_mapping_dict

In [ ]:
order = joblib.load('./order.pckle')

In [ ]:
mp_handle_name_mapping_dict = dict(zip(mp_handles, mp_names))

In [ ]:
del mp_name_vote_mapping_dict['Philippa Whitford']

In [ ]:
mp_name_vote_mapping_dict['Ruth Jones'] = 1

In [ ]:
mp_handle_vote_dict = collections.OrderedDict()

for k in final_hashtags_dict.keys():
    if mp_handle_name_mapping_dict[k] in mp_name_vote_mapping_dict.keys():
        mp_handle_vote_dict[k] = mp_name_vote_mapping_dict[mp_handle_name_mapping_dict[k]]
    
mp_handle_vote_dict

In [ ]:
joblib.dump(mp_handle_vote_dict, './all_new_test_mp_2019_brexit_vote_label.y')

In [ ]:
mp_handle_vote_dict

In [ ]:
ordered_x = collections.OrderedDict()

for k in mp_handle_vote_dict:
    ordered_x[k] = final_hashtags_dict[k]

In [ ]:
ordered_x

In [ ]:
set(mp_handle_vote_dict).difference(set(split_order))

In [ ]:
def Repeat(x): 
    _size = len(x) 
    repeated = [] 
    for i in range(_size): 
        k = i + 1
        for j in range(k, _size): 
            if x[i] == x[j] and x[i] not in repeated: 
                repeated.append(x[i]) 
    return repeated

print(Repeat(split_order))

In [ ]:
print(len(final_hashtags_dict.keys()))

In [ ]:
del ordered_x['jwhittingdale']
vectorizer = DictVectorizer()

hashtags = list(ordered_x.values())

sparse_adjacency_matrix = vectorizer.fit_transform(hashtags)
hashtags_df = pd.DataFrame(sparse_adjacency_matrix.todense(), index=ordered_x.keys()
                           , columns=vectorizer.get_feature_names())

#sparse_hashtags_df = hashtags_df.to_sparse(fill_value=0.0)

sparse_csr_matrix = sparse.csr_matrix(hashtags_df.values)

joblib.dump(sparse_csr_matrix, './all_trimmed_mp_2017_hashtags.allx') 

In [ ]:
for a, b in zip(final_hashtags_dict.keys(), mp_handle_vote_dict.keys()):
    print(a == b)

In [ ]:
for i in hashtags_df.columns:
    print("'" + i + "'" + ',')

In [ ]:
l = list(hashtags_df.columns)
import csv

with open("output.csv",'w') as resultFile:
    wr = csv.writer(resultFile)
    for item in l:
        wr.writerow([item])

In [ ]:
print(Repeat(hashtags_df.columns))

In [ ]:
!pip install umap_learn

In [ ]:
test = joblib.load('./all_vote_labels.y')

In [ ]:
new_2019_brexit_votes = {}

for k in ordered_x.keys():
    if k in test.keys():
        new_2019_brexit_votes[k] = test[k]

In [ ]:
len(new_2019_brexit_votes)

In [ ]:
joblib.dump(new_2019_brexit_votes, './all_new_2017_brexit_vote_labels.y')

In [ ]:
len(new_brexit_votes)

In [ ]:
set(mp_handle_vote_dict.keys()).difference(set(new_2019_brexit_votes.keys()))

In [ ]:
!pip show scipy

In [ ]:
!pip show joblib

In [ ]:
test = joblib.load('./ind.mps.x')

In [56]:
import numpy as np
import pandas as pd
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction import DictVectorizer
from collections import Counter
from scipy import sparse
import collections
import re
import joblib

# Custom Transformer that extracts columns passed as argument to its constructor
class TfidfFeatureExtractor(BaseEstimator, TransformerMixin):
    # Class Constructor
    def __init__(self):
        self._feature_names = None
        self._useful_hashtags = None

    def vectoriser(self, features):
        dict_vectorizer = DictVectorizer()
        hashtags = list(features.values())
        sparse_adjacency_matrix = dict_vectorizer.fit_transform(hashtags)
        hashtags_df = pd.DataFrame(sparse_adjacency_matrix.todense(), index=features.keys()
                                   , columns=dict_vectorizer.get_feature_names())
        sparse_csr_matrix = sparse.csr_matrix(hashtags_df.values)
        return sparse_csr_matrix
    
    def features_transformer(self, X):
        new_features = collections.OrderedDict()
        features = X
        for mp_handle, feature_dict in features.items():
            new_feature_dict = {}
            for feature in self._useful_hashtags:
                if feature in feature_dict:
                    new_feature_dict[feature] = feature_dict[feature]
                else:
                    new_feature_dict[feature] = 0
            new_features[mp_handle] = new_feature_dict
        return new_features

    def hashtag_deleter(self, X):
        new_features = collections.OrderedDict()
        features = X
        for mp_handle, feature_dict in features.items():
            new_feature_dict = {}
            for feature in feature_dict:
                if feature in self._useful_hashtags:
                    new_feature_dict[feature] = feature_dict[feature]
            new_features[mp_handle] = new_feature_dict
        return new_features

    def mp_deleter(self, X, y):
        features = X
        handles = list(features.keys())
        for mp_handle in handles:
            if mp_handle not in y.keys():
                del features[mp_handle]
        return features

    def sanitise(self, mps_tweets_df):
        # Sanitise author column
        mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.lower())
        mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.split()[0])
        author_contents_mps_tweets_df = mps_tweets_df[['author', 'contents']].copy()

        def extract_hash_tags(s):
            return set([re.sub(r"#+", "#", k) for k in set(
                [re.sub(r"(\W+)$", "", j, flags=re.UNICODE) for j in
                 set([i for i in s.split() if i.startswith("#")])])])

        dict_of_mps = {k: v for k, v in author_contents_mps_tweets_df.groupby('author')['contents']}
        new_dict_of_mps = {}
        for k, v in dict_of_mps.items():
            vals = []
            for val in v:
                vals.append(extract_hash_tags(val))
            new_dict_of_mps[k] = vals

        for k in new_dict_of_mps.keys():
            new_dict_of_mps[k] = [item for sublist in new_dict_of_mps[k] for item in sublist]

        return new_dict_of_mps

    def extract_features(self, all_tweets):
        all_hashtags = []
        count = 0
        for dict_of_tweets in all_tweets[:-1]:
            all_hashtags.append(self.sanitise(pd.DataFrame.from_dict(dict_of_tweets['posts'])))
        final_hashtags_dict = {}
        for dict_of_hashtags in all_hashtags:
            for k, v in dict_of_hashtags.items():
                if k in final_hashtags_dict.keys():
                    val = final_hashtags_dict[k]
                    if val != None:
                        val = val + v
                    else:
                        val = v
                    final_hashtags_dict[k] = val
                else:
                    final_hashtags_dict[k] = v
        for k in final_hashtags_dict.keys():
            final_hashtags_dict[k] = dict(Counter(final_hashtags_dict[k]))
        return final_hashtags_dict

    def extract_feature_names(self, X):
        used_hashtags = []
        for hashtag_list in X.values():
            used_hashtags += list(hashtag_list.keys())
        return list(set(used_hashtags))

    def extract_mp_handles(self, X):
        return list(X.keys())

    def extract_useful_columns(self, X):
        useful_columns = []
        for i in range(0, X.shape[1]):
            result = np.where(X[:, i] > 0)
            if 5 < len(result[0]) < 500:
                useful_columns.append(i)
        return useful_columns
    
    def transform_y(self, X, y):
        handles = list(y.keys())
        for key in handles:
            if key not in X.keys():
                del y[key]
        return y

    # Return self nothing else to do here
    def fit(self, X, y=None):
        features = self.extract_features(X)
        self._feature_names = self.extract_feature_names(features)
#         features = self.mp_deleter(features, y)
        feature_vector = self.vectoriser(features)
        useful_columns = self.extract_useful_columns(feature_vector.toarray())
        self._useful_hashtags = [self._feature_names[i] for i in useful_columns]
        return self

        # Method that describes what we need this transformer to do

    def transform(self, X, y=None):
        features = self.extract_features(X)
        if y is not None:
            features = self.mp_deleter(features, y)
        features = self.features_transformer(features)
        if y is not None:
            y = self.transform_y(features, y)
        feature_vector = self.vectoriser(features)
#         return feature_vector, y
        return TfidfTransformer().fit_transform(feature_vector).toarray(), y


In [62]:
# Custom Transformer that extracts columns passed as argument to its constructor
class TimeFeatureExtractor(BaseEstimator, TransformerMixin):
    # Class Constructor
    def __init__(self):
        self._feature_names = None
        self._useful_hashtags = None

    def vectoriser(self, features):
        dict_vectorizer = DictVectorizer()
        hashtags = list(features.values())
        sparse_adjacency_matrix = dict_vectorizer.fit_transform(hashtags)
        hashtags_df = pd.DataFrame(sparse_adjacency_matrix.todense(), index=features.keys()
                                   , columns=dict_vectorizer.get_feature_names())
        sparse_csr_matrix = sparse.csr_matrix(hashtags_df.values)
        return sparse_csr_matrix
    
    def features_transformer(self, X):
        new_features = collections.OrderedDict()
        features = X
        for mp_handle, feature_dict in features.items():
            new_feature_dict = {}
            for feature in self._useful_hashtags:
                if feature in feature_dict:
                    new_feature_dict[feature] = feature_dict[feature]
                else:
                    new_feature_dict[feature] = 0
            new_features[mp_handle] = new_feature_dict
        return new_features

    def hashtag_deleter(self, X):
        new_features = collections.OrderedDict()
        features = X
        for mp_handle, feature_dict in features.items():
            new_feature_dict = {}
            for feature in feature_dict:
                if feature in self._useful_hashtags:
                    new_feature_dict[feature] = feature_dict[feature]
            new_features[mp_handle] = new_feature_dict
        return new_features

    def mp_deleter(self, X, y):
        features = X
        handles = list(features.keys())
        for mp_handle in handles:
            if mp_handle not in y.keys():
                del features[mp_handle]
        return features

    def sanitise(self, mps_tweets_df):
        # Sanitise author column
        mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.lower())
        mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.split()[0])
        author_contents_mps_tweets_df = mps_tweets_df[['author', 'contents']].copy()

        def extract_hash_tags(s):
            return set([re.sub(r"#+", "#", k) for k in set(
                [re.sub(r"(\W+)$", "", j, flags=re.UNICODE) for j in
                 set([i for i in s.split() if i.startswith("#")])])])

        dict_of_mps = {k: v for k, v in author_contents_mps_tweets_df.groupby('author')['contents']}
        new_dict_of_mps = {}
        for k, v in dict_of_mps.items():
            vals = []
            for val in v:
                vals.append(extract_hash_tags(val))
            new_dict_of_mps[k] = vals

        for k in new_dict_of_mps.keys():
            new_dict_of_mps[k] = [item for sublist in new_dict_of_mps[k] for item in sublist]

        return new_dict_of_mps

    def extract_features(self, all_tweets):
        all_hashtags = []
        count = 0
        for dict_of_tweets in all_tweets[:-1]:
            all_hashtags.append(self.sanitise(pd.DataFrame.from_dict(dict_of_tweets['posts'])))
        final_hashtags_dict = {}
        for dict_of_hashtags in all_hashtags:
            for k, v in dict_of_hashtags.items():
                if k in final_hashtags_dict.keys():
                    val = final_hashtags_dict[k]
                    if val != None:
                        val = val + v
                    else:
                        val = v
                    final_hashtags_dict[k] = val
                else:
                    final_hashtags_dict[k] = v
        for k in final_hashtags_dict.keys():
            final_hashtags_dict[k] = dict(Counter(final_hashtags_dict[k]))
        return final_hashtags_dict

    def extract_feature_names(self, X):
        used_hashtags = []
        for hashtag_list in X.values():
            used_hashtags += list(hashtag_list.keys())
        return list(set(used_hashtags))

    def extract_mp_handles(self, X):
        return list(X.keys())

    def extract_useful_columns(self, X):
        useful_columns = []
        for i in range(0, X.shape[1]):
            result = np.where(X[:, i] > 0)
            if 5 < len(result[0]) < 500:
                useful_columns.append(i)
        return useful_columns
    
    def transform_y(self, X, y):
        handles = list(y.keys())
        for key in handles:
            if key not in X.keys():
                del y[key]
        return y

    # Return self nothing else to do here
    def fit(self, X, y=None):
        return self

        # Method that describes what we need this transformer to do

    def transform(self, X, y=None):
        if y is not None:
            features = self.mp_deleter(X, y)
        if y is not None:
            y = self.transform_y(features, y)
        return feature_vector, y

In [43]:
transformer = TfidfFeatureExtractor()

In [28]:
testing = joblib.load('./mps_2017_tweets.pckle')

In [29]:
validator = joblib.load('./all_mp_2017_hashtags.allx')

In [33]:
test_x = []
test_x1 = transformer.fit(testing)
test_x, y = test_x1.transform(testing)

  (0, 90)	1.0
  (0, 161)	1.0
  (0, 179)	1.0
  (0, 180)	87.0
  (0, 212)	3.0
  (0, 343)	9.0
  (0, 378)	1.0
  (0, 601)	1.0
  (0, 817)	1.0
  (0, 821)	1.0
  (0, 824)	11.0
  (0, 859)	1.0
  (0, 1022)	1.0
  (0, 1023)	3.0
  (0, 1491)	1.0
  (0, 1721)	1.0
  (0, 1749)	1.0
  (0, 2315)	2.0
  (0, 2410)	20.0
  (0, 2642)	1.0
  (0, 2643)	1.0
  (0, 3569)	4.0
  (0, 3722)	1.0
  (0, 3984)	1.0
  (0, 4051)	1.0
  :	:
  (547, 9221)	1.0
  (547, 22895)	1.0
  (548, 2538)	1.0
  (548, 8784)	2.0
  (548, 9248)	2.0
  (548, 9249)	2.0
  (548, 9838)	1.0
  (548, 12617)	1.0
  (548, 14430)	1.0
  (548, 16096)	1.0
  (548, 16100)	1.0
  (548, 17235)	1.0
  (548, 20288)	1.0
  (548, 22022)	5.0
  (548, 28035)	1.0
  (549, 11481)	2.0
  (549, 13833)	1.0
  (549, 13838)	1.0
  (549, 16120)	1.0
  (550, 5451)	1.0
  (550, 24984)	1.0
  (551, 11235)	1.0
  (551, 25912)	1.0
  (552, 12565)	1.0
  (552, 13833)	1.0


In [34]:
validator.toarray() == test_x.toarray()

array([[ True,  True,  True, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True],
       ...,
       [ True,  True,  True, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True]])

In [25]:
print(test_x)

[]


In [ ]:
print(validator)

In [63]:
from sklearn.linear_model import LogisticRegression

x = joblib.load('./2017vectors100.x')
y = joblib.load('./all_trimmed_mp_2017_brexit_vote_label.y')
real_y = list(y.values())
future_x = joblib.load('./2019vectors100.x')
future_y = joblib.load('./all_new_2019_no_confidence_vote_labels.y')
real_future_y = list(future_y.values())

In [82]:
real_y

{'alanmakmp': 1,
 'albertowenmp': 0,
 'alexsobel': 0,
 'alisonthewliss': 0,
 'andrew4pendle': 1,
 'angusmacneilsnp': 0,
 'anneliesedodds': 0,
 'borisjohnson': 1,
 'carolynharris24': 0,
 'chrislawsnp': 0,
 'cpjelmore': 0,
 'danirowley': 0,
 'davidlammy': 0,
 'dawnbutlerbrent': 0,
 'edvaizey': 1,
 'geraintdaviesmp': 0,
 'greghands': 1,
 'guyopperman': 1,
 'hannahb4livimp': 0,
 'huddlestonnigel': 1,
 'jeremy_hunt': 1,
 'jimfromoldham': 0,
 'jonathanplaid': 0,
 'jostevenslabour': 0,
 'jwoodcockmp': 0,
 'karlturnermp': 0,
 'kerrymp': 0,
 'lukepollard': 0,
 'marcus4nuneaton': 1,
 'martinjdocherty': 0,
 'marycreaghmp': 0,
 'mikegapes': 0,
 'onnmel': 0,
 'pgibsonsnp': 0,
 'rees4neath': 0,
 'richardbenyonmp': 1,
 'ruthcadbury': 0,
 'sarahchampionmp': 0,
 'sdoughtymp': 0,
 'stellacreasy': 0,
 'theresecoffey': 1,
 'thomasbrake': 0,
 'tobias_ellwood': 1,
 'wesstreeting': 0,
 'willquince': 1,
 'barrysheerman': 0,
 'chionwurah': 0,
 'coyleneil': 0,
 'davidlinden': 0,
 'emmadentcoad': 0,
 'jessphilli

In [64]:
transformer = TimeFeatureExtractor()

In [65]:
transformer = transformer.fit(x, y)
x, real_y = transformer.transform(x, y)
future_x, future_y = transformer.transform(future_x, future_y)

AttributeError: 'list' object has no attribute 'keys'

In [69]:
from sklearn.metrics import classification_report

reg = LogisticRegression()
# reg.fit(x, list(real_y.values()))
# predictions = reg.predict(future_x)
reg.fit(x, real_y)
predictions = reg.predict(x)

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


ValueError: Found input variables with inconsistent numbers of samples: [556, 511]

In [ ]:
import tensorflow as tf
from tensorflow import keras

model = keras.Sequential([
    keras.layers.Dense(64, activation=tf.nn.leaky_relu),
    keras.layers.Dense(32, activation=tf.nn.relu),
    keras.layers.Dense(2, activation=tf.nn.softmax)
])

model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])

model.fit(x.toarray(), np.array(real_y), epochs=10)

probabilities = model.predict(future_x.toarray())

In [61]:
print(classification_report(np.array(list(future_y.values())), predictions, labels=[0,1]))

              precision    recall  f1-score   support

           0       0.40      0.46      0.43       248
           1       0.49      0.44      0.46       301

    accuracy                           0.44       549
   macro avg       0.45      0.45      0.44       549
weighted avg       0.45      0.44      0.45       549



In [ ]:
print(np.array(list(future_y.values())))

In [ ]:
predictions = []
for p in probabilities:
    if p[0] > p[1]:
        predictions.append(0)
    else:
        predictions.append(1)

In [ ]:
future_x.shape

In [ ]:
print(len(predictions))

In [ ]:
print(x)

In [ ]:
test = joblib.load('./mps_tweets.pckle')

In [ ]:
print(test)

In [ ]:
!pip install nltk

In [10]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import joblib
import pandas as pd
import numpy as np
from nltk.tokenize import TweetTokenizer

import nltk
nltk.download('punkt')
nltk.download('stopwords')

[nltk_data] Downloading package punkt to /Users/jf/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /Users/jf/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [27]:
all_tweets = joblib.load('./mps_2017_tweets.pckle')

all_sentences = []
 
def extract_sentences(mps_tweets_df):
    mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.lower())
    mps_tweets_df['author'] = mps_tweets_df['author'].apply(lambda x: x.split()[0])

    author_contents_mps_tweets_df = mps_tweets_df[['author', 'contents']].copy()

    dict_of_mps = {k: v for k, v in author_contents_mps_tweets_df.groupby('author')['contents']}
    new_dict_of_mps = {}

    for k, v in dict_of_mps.items():
        vals = []
        for val in v:
            tokeniser = TweetTokenizer()
            tokens = tokeniser.tokenize(val)
            filtered_sentence = [w for w in tokens if not w in stopwords.words()]
            vals.append(filtered_sentence)
        new_dict_of_mps[k] = vals
    
    '''
    for k in new_dict_of_mps.keys():
        new_dict_of_mps[k] = [item for sublist in new_dict_of_mps[k] for item in sublist]
    '''

    return new_dict_of_mps

for dict_of_tweets in all_tweets[:-1]:
    all_sentences.append(extract_sentences(pd.DataFrame.from_dict(dict_of_tweets['posts'])))

In [71]:
all_sentences[1]

{'alanmakmp': [['My',
   '#2017',
   'NewYear',
   'message',
   ':',
   'economy',
   '&',
   'communities',
   'across',
   '#Havant',
   'constituency',
   'strong',
   "I'll",
   'continue',
   'working',
   'hard',
   'residents',
   'https://t.co/EFrmT1TjAK']],
 'alexsobel': [['The',
   'latest',
   'The',
   'alexsobel',
   'Daily',
   '!',
   'https://t.co/V3RfQncOT6',
   'Thanks',
   '@4joturner',
   '@TheIanCruise',
   '@JohnRoss43',
   '#yorkshire',
   '#technology']],
 'andrew4pendle': [['We',
   'always',
   'make',
   'plans',
   'give',
   'things',
   'New',
   'Year',
   'give',
   '?',
   '#GiveBlood',
   '2017',
   'https://t.co/GYChwZ5T9s'],
  ['Transport',
   'chief',
   'praises',
   'Lancashire',
   "Telegraph's",
   "'",
   'Stop',
   'Madness',
   "'",
   'campaign',
   'reply',
   '#Pendle',
   'MP',
   'https://t.co/wcPEteTHB5']],
 'angusmacneilsnp': [['Labours',
   'antics',
   'Babybox',
   'level',
   'cynical',
   'goal',
   'short-termism',
   'Lib',
   

In [28]:
sentences_to_sample = []
for day in all_sentences:
    for sentence in day.values():
        sentences_to_sample += sentence

In [185]:
sentences_to_sample

[['With',
  '.',
  'Brilliance',
  'massive',
  'challenges',
  '.',
  'Wirralians',
  ':',
  'forget',
  'walk',
  'centres',
  '&',
  'GP',
  'hours',
  '#proud',
  '#NHS',
  'https://t.co/X5wvOJV5RX'],
 ['Congratulations',
  'Cllr',
  '.',
  'Viddy',
  'Persaud',
  '@ViddyHavering',
  'Cllr',
  '.',
  'Robert',
  'Benham',
  '@CllrRobBenham',
  'Tim',
  'Ryan',
  'amazing',
  'day',
  'community',
  'action',
  'engagement',
  'throughout',
  'Rush',
  'Green',
  ',',
  'Crowlands',
  'Lower',
  'Mawneys',
  '(',
  'Romford',
  ')',
  'New',
  'Year',
  '’',
  'Day',
  ',',
  '2018',
  '!',
  '#KeepHaveringSpecial',
  '#Brooklands',
  'https://t.co/CsfbmEXLEA'],
 ['Having',
  'great',
  'New',
  'Year',
  '’',
  'Day',
  'campaigning',
  'teams',
  'across',
  'Romford',
  '-',
  'Marusha',
  'Emmanuel',
  'day',
  ',',
  'going',
  'around',
  'London',
  'Road',
  'area',
  '-',
  'local',
  'people',
  'enthusiastically',
  'backing',
  'campaign',
  '“',
  'Keep',
  'Havering',


In [29]:
from random import sample

limit = len(sentences_to_sample)

for sentence in range(0, limit):
    temp = sample(sentences_to_sample[sentence], len(sentences_to_sample[sentence]))
    sentences_to_sample += temp

In [ ]:
len(sentences_to_sample)

In [30]:
import multiprocessing
from time import time
from gensim.models import Word2Vec

cores = multiprocessing.cpu_count() # Count the number of cores in a computer
cores

w2v_model = Word2Vec(min_count=1,
                     window=2,
                     size=100,
                     sample=6e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=cores-1)

t = time()

w2v_model.build_vocab(sentences_to_sample, progress_per=10000)

print('Time to build vocab: {} mins'.format(round((time() - t) / 60, 2)))

t = time()

w2v_model.train(sentences_to_sample, total_examples=w2v_model.corpus_count, epochs=50, report_delay=1)

print('Time to train the model: {} mins'.format(round((time() - t) / 60, 2)))

w2v_model.init_sims(replace=True)

Time to build vocab: 0.07 mins
Time to train the model: 2.83 mins


In [31]:
w2v_model.wv.most_similar(positive=["#Remain"])

[('Remain', 0.6510682106018066),
 ('#Leave', 0.6003544330596924),
 ('26k', 0.5957266688346863),
 ('overwhelmingly', 0.5891056060791016),
 ('https://t.co/CaDCo7Bif6', 0.5890083312988281),
 ('https://t.co/sUkEtqAosf', 0.5860649943351746),
 ('instigation', 0.5829588770866394),
 ('treble', 0.5825820565223694),
 ('https://t.co/Tg1OJKiJZI', 0.5793086886405945),
 ('dud', 0.5784189105033875)]

In [181]:
w2v_model.wv.doesnt_match(['#Brexit', '#Leave', '#Remain'])

'#Brexit'

In [33]:
w2v_model.save("w2v_model2018.model")

In [7]:
from gensim.models import Word2Vec
w2v_model = Word2Vec.load("w2v_model.model")

In [34]:
embedding_dict = collections.OrderedDict()

for k, v in final_hashtags_dict.items():
    new_mp_dict = {}
    for hashtag, count in v.items():
        l = list(w2v_model.wv.vocab.keys())
        if hashtag in l:
            new_mp_dict[hashtag] = w2v_model[hashtag]
    embedding_dict[k] = new_mp_dict
        

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:8: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  


In [168]:
embedding_dict['alanmakmp']

{'#Havant': array([-0.1780894 ,  0.15855499,  0.13072194,  0.01914952,  0.24596214,
         0.07022328,  0.1341838 ,  0.04259848,  0.30946326,  0.02894506,
        -0.09776531, -0.04653049, -0.00689694,  0.05846357,  0.08150503,
        -0.04893401,  0.00256958, -0.09620246, -0.13156171,  0.2783191 ,
         0.02777995, -0.05703832, -0.0414306 , -0.07741667, -0.07034887,
        -0.03085292, -0.2099498 ,  0.05787875,  0.00095338, -0.03004238,
        -0.01372403,  0.14146665,  0.03169726,  0.15819913,  0.0777838 ,
        -0.04212258,  0.02117902,  0.02882315,  0.06840289,  0.04710034,
         0.13338543,  0.01818318,  0.12202717,  0.07199475,  0.02294618,
        -0.057459  , -0.01863864,  0.05515121, -0.03411524, -0.00544913,
         0.02809435,  0.00288147,  0.0967026 ,  0.03869272, -0.16701245,
         0.09596584,  0.11908916, -0.06527846, -0.059432  ,  0.00979268,
         0.09557   ,  0.02171516,  0.07599188, -0.20859493, -0.08402845,
         0.10773464, -0.01504065, -0.038

In [166]:
vectorizer = DictVectorizer()

hashtags = list(embedding_dict.values())

sparse_adjacency_matrix = vectorizer.fit_transform(hashtags)
hashtags_df = pd.DataFrame(sparse_adjacency_matrix.todense(), index=embedding_dict.keys()
                           , columns=vectorizer.get_feature_names())

#sparse_hashtags_df = hashtags_df.to_sparse(fill_value=0.0)

sparse_csr_matrix = sparse.csr_matrix(hashtags_df.values)

ValueError: Sample sequence X is empty.

In [28]:
type(hashtags)

list

In [29]:
hashtags

[{'#HappyNewYear': array([-0.21111156,  0.00436352,  0.23832174, -0.16586195, -0.6645525 ,
          0.16931929,  0.50224257, -0.25313854,  0.2787038 , -0.08248554],
        dtype=float32),
  '#Havant': array([-0.21579906, -0.04654038,  0.4581266 ,  0.26550728,  0.09506274,
          0.43392232, -0.08919441,  0.5892474 , -0.01802612, -0.3436162 ],
        dtype=float32),
  '#4IR': array([ 0.14495312,  0.6972469 ,  0.24844886,  0.44877392, -0.04510712,
         -0.27500206,  0.2373684 ,  0.17792092,  0.21745604,  0.12947236],
        dtype=float32),
  '#APPG': array([ 0.0214682 ,  0.6056044 ,  0.2870631 ,  0.19256629,  0.15703766,
         -0.1324467 ,  0.04641093,  0.29543316,  0.46142033, -0.41079065],
        dtype=float32),
  '#IndustrialStrategy': array([ 0.24548703,  0.4405045 ,  0.468969  ,  0.36554557,  0.07412443,
         -0.20846108,  0.22037914,  0.5418637 , -0.02981028,  0.01068721],
        dtype=float32),
  '#2017': array([-0.0141643 ,  0.317939  ,  0.13871719, -0.2963107

In [35]:
vector_average_dict = collections.OrderedDict()

for key, value in embedding_dict.items():
    vectors = value.values()
    average_vector = [0] * 100
    for k, v in value.items():
        average_vector += v
    average_vector = average_vector/len(list(value.values()))
    vector_average_dict[key] = average_vector

In [33]:
test = embedding_dict['alanmakmp']

average_vector = [0,0,0,0,0,0,0,0,0,0]
for k, v in test.items():
    print("before ", average_vector)
    print("vector ", v)
    average_vector += v
    print("after ", average_vector)
average_vector = average_vector/len(list(test.values()))

before  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
vector  [-0.21111156  0.00436352  0.23832174 -0.16586195 -0.6645525   0.16931929
  0.50224257 -0.25313854  0.2787038  -0.08248554]
after  [-0.21111156  0.00436352  0.23832174 -0.16586195 -0.66455251  0.16931929
  0.50224257 -0.25313854  0.27870381 -0.08248554]
before  [-0.21111156  0.00436352  0.23832174 -0.16586195 -0.66455251  0.16931929
  0.50224257 -0.25313854  0.27870381 -0.08248554]
vector  [-0.21579906 -0.04654038  0.4581266   0.26550728  0.09506274  0.43392232
 -0.08919441  0.5892474  -0.01802612 -0.3436162 ]
after  [-0.42691062 -0.04217687  0.69644834  0.09964533 -0.56948977  0.60324161
  0.41304816  0.33610886  0.26067768 -0.42610173]
before  [-0.42691062 -0.04217687  0.69644834  0.09964533 -0.56948977  0.60324161
  0.41304816  0.33610886  0.26067768 -0.42610173]
vector  [ 0.14495312  0.6972469   0.24844886  0.44877392 -0.04510712 -0.27500206
  0.2373684   0.17792092  0.21745604  0.12947236]
after  [-0.28195751  0.65507004  0.9448972   0

  0.23188712  0.17901635  0.40231553 -0.3109229 ]
after  [-32.34458953  48.41017336  37.60438443  34.06175888 -22.01652055
   6.35149359  31.5053699   27.8738326   40.4788959    6.10815403]
before  [-32.34458953  48.41017336  37.60438443  34.06175888 -22.01652055
   6.35149359  31.5053699   27.8738326   40.4788959    6.10815403]
vector  [ 0.03175339  0.34536752  0.4971998   0.21118794 -0.38683254 -0.2386801
  0.48320976  0.12604468 -0.25539842  0.25824448]
after  [-32.31283614  48.75554088  38.10158424  34.27294682 -22.40335308
   6.1128135   31.98857966  27.99987728  40.22349748   6.36639852]
before  [-32.31283614  48.75554088  38.10158424  34.27294682 -22.40335308
   6.1128135   31.98857966  27.99987728  40.22349748   6.36639852]
vector  [-0.3016035  -0.14611167 -0.20573226  0.602296    0.33220455  0.04345605
 -0.05425851  0.55607873 -0.23468055  0.05576459]
after  [-32.61443963  48.60942921  37.89585198  34.87524282 -22.07114853
   6.15626955  31.93432115  28.55595601  39.98881693  

In [32]:
average_vector

array([-0.20360626,  0.29806033,  0.15662842,  0.15258113, -0.18565472,
        0.01218489,  0.19439722,  0.14282108,  0.26281785,  0.00594113])

In [34]:
len(test.values())

316

In [41]:
len(list(vector_average_dict.keys()))

570

In [20]:
vectors_x = list(vector_average_dict.values())

In [70]:
joblib.dump(vector_average_dict, '2017vectorsdict100.x')

['2017vectorsdict100.x']

In [173]:
list(vectors_x)

[array([-4.22027787e-02, -1.00782533e-01,  1.96784343e-02, -1.55304353e-02,
         4.52005445e-02, -4.13745497e-02, -4.17915573e-02, -3.73071644e-02,
         3.57740810e-02, -8.40785880e-03, -3.86057910e-02,  2.66840234e-03,
         1.13138575e-02, -4.48376863e-02, -3.97331265e-02,  6.28465038e-02,
         7.54574515e-02, -2.09107466e-02, -4.40064424e-02,  3.70388137e-02,
         2.80893068e-02,  6.75900271e-02, -2.50749929e-02,  6.99146095e-02,
        -3.93608965e-03, -6.89753586e-03, -5.98150709e-02,  3.31096705e-02,
        -5.85510481e-02,  3.16899945e-02, -4.62969328e-02,  2.74024575e-02,
        -2.49811504e-02,  4.20768867e-02, -2.80261449e-02,  3.01286207e-02,
         6.69642340e-02, -5.22099569e-02, -3.86332996e-02,  9.74513463e-03,
         5.30629492e-02,  6.79364002e-03, -1.73508522e-02,  3.58732294e-02,
         2.82313654e-02, -3.18525064e-03, -9.12127857e-03,  2.41884343e-02,
         1.20553718e-02,  1.53043188e-02, -4.45446443e-02,  7.67915436e-03,
        -1.0

In [73]:
from gensim.models import Doc2Vec
d2v_model = Word2Vec.load("d2v_model.model")

In [81]:
embedding_dict = collections.OrderedDict()

for k in final_hashtags_dict.keys():
    embedding_dict[k] = d2v_model.docvecs[k]

In [82]:
embedding_dict

OrderedDict([('alanmakmp',
              array([ 0.14672916,  0.00049288,  0.19722465, -0.0308378 , -0.00504708,
                     -0.02282159, -0.19962622,  0.0586798 , -0.07874813,  0.10426841,
                      0.01180352,  0.08705536, -0.14323299, -0.02608656,  0.04633541,
                     -0.19059308,  0.0221165 ,  0.1073276 ,  0.08614826,  0.00720284,
                      0.07371093,  0.00912861,  0.18637107, -0.01349215, -0.02962886,
                     -0.09730717,  0.02885146, -0.02913118,  0.03954205,  0.16510107,
                     -0.03384827,  0.09358162,  0.1093689 ,  0.01939577, -0.08302216,
                     -0.11674055, -0.09875209, -0.0135946 ,  0.04451691, -0.08016903,
                     -0.12947781, -0.07153033, -0.08459588, -0.14519165,  0.02055088,
                     -0.02450044, -0.04329295,  0.12511097,  0.14936993, -0.03981624,
                     -0.00640817, -0.08051052,  0.10027934,  0.14167324,  0.1508563 ,
                     -0.059

In [83]:
vectors_x = list(embedding_dict.values())

In [84]:
joblib.dump(vectors_x, 'mpdocvectorsdict100.x')

['mpdocvectorsdict100.x']